# Zusammenfassung der Analysen vom Hackathon für die Webside

- womöglich zur Darstellung auf der Webside


In [2]:
import numpy as np
import pandas as pd
import altair as alt

## Daten aufbereitung

Dump der Datenbank vom 25.03.2023. Die verschiedene Tabellen der Datenbank werden einzeln eingelesen. Zusätzlich werden alle direkt zu einem Tweet zugehörige Information in ein Datenobjekt gesammelt. Die Informationen zu den GIS-Daten zu den einzelnen Polizeistadtion ("police_stations") sind noch unvollständig und müssen gegebenfalls nocheinmal überprüft werden.



In [117]:
tweets_meta = pd.concat([pd.read_csv("data/entity_old.tsv", sep = "\t"), # data from old scraper
                         pd.read_csv("data/tweets.csv")]) # data from new scraper

tweets_text = pd.concat([pd.read_csv("data/tweet_old.tsv", sep = "\t")[['id', 
                                                                        'tweet_text', 
                                                                        'created_at', 
                                                                        'user_id']].rename(columns = {"id":"tweet_id"}),
                         pd.read_csv("data/tweets-1679742698645.csv")])

tweets_statistics = pd.concat([pd.read_csv("data/tweet_old.tsv", sep = "\t")[['id', 
                                                                              'like_count', 
                                                                              'retweet_count', 
                                                                              'reply_count', 
                                                                              'quote_count']].rename(columns = {"id":"tweet_id"}),
                              pd.read_csv("data/tweets-1679742620302.csv")])

tweets_user = pd.read_csv("data/user_old.tsv", 
                          sep = "\t").rename(columns = {"id":"user_id","name": "user_name"}
                                            ).merge(pd.read_csv("data/tweets-1679742702794.csv"
                                                               ).rename(columns = {"username":"handle", "handle": "user_name"}),
                                                   on = "user_id",
                                                   how = "outer",
                                                   suffixes = ["_2021", "_2022"])

# Some usernames corresponding to one user_id have changed overtime. For easier handling only the latest username and handle is kept
tweets_user = tweets_user.assign(handle    = tweets_user.apply(lambda row: row['handle_2021'] if pd.isna(row['handle_2022']) else row['handle_2022'], axis=1),
                                 user_name = tweets_user.apply(lambda row: row['user_name_2021'] if pd.isna(row['user_name_2022']) else row['user_name_2022'], axis=1)
                                ).drop(['handle_2021', 'handle_2022', 'user_name_2021', 'user_name_2022'], axis =1)

police_stations = pd.read_csv("data/polizei_accounts_geo.csv", sep = "\t"  # addiditional on police stations
                             ).rename(columns = {"Polizei Account": "handle"})

tweets_meta.shape, tweets_statistics.shape, tweets_text.shape, tweets_user.shape

((479991, 3), (151690, 8), (151690, 4), (13327, 3))

Jetzt können noch alle Tweet bezogenen informationen in einem Data Frame gespeichert werden:

In [118]:
# Merge like statistics, tweet text and user information in one data frame
tweets_combined = pd.merge(tweets_statistics, 
                           tweets_text,
                           on = 'tweet_id').merge(tweets_user, on = 'user_id'
                                                 ).drop(['id'], axis = 1) # drop unascessary id column (redundant to index)
 

In [119]:
# Convert Counts to integer values
tweets_combined[['like_count', 'retweet_count', 'reply_count', 'quote_count']] = tweets_combined[['like_count', 'retweet_count', 'reply_count', 'quote_count']].fillna(-99).astype(int)
tweets_combined = tweets_combined.assign(measured_at = pd.to_datetime(tweets_combined['measured_at']), # change date to date format
                                         created_at  = pd.to_datetime(tweets_combined['created_at']),
                                         handle      = tweets_combined['handle'].str.lower(),
                                         is_deleted  = tweets_combined['is_deleted'].map(lambda x: False if x == 0.0 else ( True if x == 1.0 else np.nan)))
tweets_combined

/nix/store/4105l1v2llsjz4j7qaqsz0fljc9z0z2r-python3-3.10.9-env/lib/python3.10/site-packages/IPython/lib/pretty.py:778: FutureWarning: In a future version, object-dtype columns with all-bool values will not be included in reductions with bool_only=True. Explicitly cast to bool dtype instead.
  output = repr(obj)
/nix/store/4105l1v2llsjz4j7qaqsz0fljc9z0z2r-python3-3.10.9-env/lib/python3.10/site-packages/IPython/core/formatters.py:342: FutureWarning: In a future version, object-dtype columns with all-bool values will not be included in reductions with bool_only=True. Explicitly cast to bool dtype instead.
  return method()


tweet_id  like_count  retweet_count  reply_count  \
0       1321021123463663616           2              1            2   
1       1321037834246066181           2              0            0   
2       1321068234955776000          19              3            3   
3       1321073940199100416           0              0            0   
4       1321088646506754049           2              0            0   
...                     ...         ...            ...          ...   
151685  1625828803804004354           5              1            1   
151686  1628004105623900167           2              0            0   
151687  1628004810183016448           6              0            0   
151688  1628352896352878593           2              0            0   
151689  1628709531998998529          10              1            0   

        quote_count         measured_at is_deleted  \
0                 0                 NaT        NaN   
1                 0                 NaT        NaN   
2                 0                 NaT        NaN   
3                 0                 NaT        NaN   
4                 0                 NaT        NaN   
...             ...                 ...        ...   
151685            0 2023-02-19 13:40:36      False   
151686            0 2023-02-25 13:14:49      False   
151687            0 2023-02-25 13:14:49      False   
151688            0 2023-02-26 13:15:05      False   
151689            0 2023-02-27 12:17:33      False   

                                               tweet_text          created_at  \
0       @mahanna196 Da die Stadt keine Ausnahme für Ra... 2020-10-27 09:29:13   
1                                     @mahanna196 Ja. *sr 2020-10-27 10:35:38   
2       #Aktuell Auf dem ehem. Bundeswehrkrankenhausge... 2020-10-27 12:36:26   
3       @Emma36166433 Bitte lesen Sie unseren Tweet 2/... 2020-10-27 12:59:06   
4       In der vergangenen Woche wurde die Wohnung des... 2020-10-27 13:57:32   
...                                                   ...                 ...   
151685  #Sicherheit durch #Sichtbarkeit\nUnsere #Dir3 ... 2023-02-15 12:06:07   
151686  Unser Präventionsteam vom #A44 berät heute und... 2023-02-21 12:10:00   
151687  Auch unser #A52 war heute aktiv und hat zum Th... 2023-02-21 12:12:48   
151688  Gestern führte unser #A13 in einer Wohnsiedlun... 2023-02-22 11:15:58   
151689  Auf dem Gelände der @BUFAStudios (Oberlandstr.... 2023-02-23 10:53:07   

                    user_id           handle  \
0        778895426007203840       polizei_ol   
1        778895426007203840       polizei_ol   
2        778895426007203840       polizei_ol   
3        778895426007203840       polizei_ol   
4        778895426007203840       polizei_ol   
...                     ...              ...   
151685  1168873095614160896  polizeiberlin_p   
151686  1168873095614160896  polizeiberlin_p   
151687  1168873095614160896  polizeiberlin_p   
151688  1168873095614160896  polizeiberlin_p   
151689  1168873095614160896  polizeiberlin_p   

                                user_name  
0       Polizei Oldenburg-Stadt/Ammerland  
1       Polizei Oldenburg-Stadt/Ammerland  
2       Polizei Oldenburg-Stadt/Ammerland  
3       Polizei Oldenburg-Stadt/Ammerland  
4       Polizei Oldenburg-Stadt/Ammerland  
...                                   ...  
151685          Polizei Berlin Prävention  
151686          Polizei Berlin Prävention  
151687          Polizei Berlin Prävention  
151688          Polizei Berlin Prävention  
151689          Polizei Berlin Prävention  

[151690 rows x 12 columns]

### Adjazenzmatrix mentions
 
Information, welche nicht direkt enthalten ist: welche Accounts werden erwähnt. Ist nur im Tweet mit @handle gekennzeichnet.

In [53]:
# TODO

0    Auch wir schließen uns dem Apell an! \n\n#Ukra...
1    @BWeltenbummler Sehr schwer zu sagen. Die Evak...
2    Halten Sie durch – die Evakuierung ist fast ab...
3    Halten Sie durch – die Evakuierung ist fast ab...
4    RT @drkberlin_iuk: 🚨 In enger Abstimmung mit d...
Name: tweet_text, dtype: object

## Metadaten 

Welche Daten bilden die Grundlage?

In [112]:
tweets_meta["entity_type"].value_counts()
# tweets_meta[tweets_meta['entity_type'] == "mention"]

hashtag    267255
url        141594
mention     71142
Name: entity_type, dtype: int64

Insgesamt haben wir 151690 einzigartige Tweets:

In [113]:
tweets_combined["tweet_id"].value_counts().shape[0] # Anzahl an Tweets

151690

In [114]:
print("Die Tweets wurden vom ", tweets_combined['created_at'].min().date(), "bis zum:", tweets_combined['created_at'].max().date(), "gesammelt.", "Also genau insgesamt:", (tweets_combined['created_at'].max() - tweets_combined['created_at'].min()).days, "Tage. (Mit kleinen Unterbrechungen)")
# tweets_combined[tweets_combined['created_at'] == tweets_combined['created_at'].max()] # Tweets vom letzten Tag

Die Tweets wurden vom  2020-10-27 bis zum: 2023-03-16 gesammelt. Also genau insgesamt: 870 Tage. (Mit kleinen Unterbrechungen)


Welche Polizei Accounts haben am meisten getweetet?

In [122]:
tweets_agg = tweets_combined.groupby(by = ["user_id", "user_name", "handle"]
                                    )["user_id"].aggregate(['count']
                                                          ).merge(police_stations,
                                                                  on = "handle",
                                                                  how = "left"
                                                                 ).sort_values(['count'], ascending=False)
tweets_agg.shape
activy_police_vis = tweets_agg[0:50]
activy_police_vis.head()

handle  count             Name      Typ           Bundesland  \
11     polizei_ffm   5512              NaN      NaN                  NaN   
0   polizeisachsen   5340  Polizei Sachsen  Polizei              Sachsen   
3   polizei_nrw_do   4895   Polizei NRW DO  Polizei  Nordrhein-Westfalen   
92       polizeibb   4323              NaN      NaN                  NaN   
61  polizeihamburg   4042  Polizei Hamburg  Polizei              Hamburg   

       Stadt         LAT        LONG  
11       NaN         NaN         NaN  
0    Dresden  51.0493286  13.7381437  
3   Dortmund  51.5142273   7.4652789  
92       NaN         NaN         NaN  
61   Hamburg   53.550341   10.000654

Visualisierung aktivste Polizeistadtionen:

In [123]:
barchart = alt.Chart(activy_police_vis[0:15]).mark_bar().encode(
    x = 'count:Q',
    y = alt.Y('handle:N', sort = '-x'),
)
barchart 

/nix/store/4105l1v2llsjz4j7qaqsz0fljc9z0z2r-python3-3.10.9-env/lib/python3.10/site-packages/altair/utils/core.py:317: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for col_name, dtype in df.dtypes.iteritems():


alt.Chart(...)

Welche Tweets ziehen besonders viel Aufmerksamkeit auf sich?

In [125]:
tweets_attention = tweets_combined.merge(police_stations,
                                         on = "handle",
                                         how = "left")
pd.options.display.max_colwidth = 100
tweets_attention.sort_values('like_count', ascending = False).reset_index()['tweet_text']



0         Die Gewalt, die unsere Kolleginnen &amp; Kollegen in der Silvesternacht erleben mussten, ist une...
1         An diejenigen, die vergangene Nacht in eine Schule in #Gesundbrunnen eingebrochen sind und 242 T...
2         WICHTIGE Info:\nÜber das Internet wird derzeit ein Video verbreitet, in dem von einem Überfall a...
3         Die Experten gehen derzeit davon aus, dass es sich um ein absichtliches "Fake-Video" handelt, da...
4                                             Weil wir dich schieben! @BVG_Kampagne 😉 https://t.co/N8kdlCxhz2
                                                         ...                                                 
151685    Sinken die Temperaturen ❄, steigt zeitgleich das Risiko für Verkehrsteilnehmer. Höchste Zeit zu ...
151686    📺Am Sonntag, um 19:50 Uhr, geht es bei #KripoLive im \n@mdrde\n auch um die Fahndung nach einem ...
151687    Musik verbindet!\nUnser #Adventskalender der #Bundespolizei startet morgen ➡ https://t.co/V6CaTV...
151688    

In [90]:
old = pd.read_csv("data/user_old.tsv",sep = "\t").rename(columns = {"id":"user_id","name": "user_name"} )
new = pd.read_csv("data/tweets-1679742702794.csv").rename(columns = {"username":"handle", "handle": "user_name"})
new

user_id          handle         user_name
0      1000004686156652545        6jannik9  Systemstratege: 
1      1000043230870867969         LSollik        Physiolucy
2      1000405847460151296   Achim1949Hans  Systemstratege: 
3      1000460805719121921          WahreW        WahreWorte
4      1000744009638252544        derD1ck3        Ⓓ①ⓒⓚ①③ (🏡)
...                    ...             ...               ...
11554             99931264       Havok1975  Systemstratege: 
11555   999542638226403328  Madame_de_Saxe  Systemstratege: 
11556   999901133282754560   tungstendie74  Systemstratege: 
11557   999904275080794112     _danielheim  Systemstratege: 
11558   999955376454930432      amyman6010  Systemstratege: 

[11559 rows x 3 columns]

In [121]:
tweets_combined.groupby(by = ["user_id", "user_name"]
                                    )["user_id"].aggregate(['count']
                                                          )

count
user_id             user_name                
223758384           Polizei Sachsen      5340
259607457           Polizei NRW K        2544
424895827           Polizei Stuttgart    1913
769128278           Polizei NRW DO       4895
775664780           Polizei Rostock       604
...                                       ...
1169206134189830145 Polizei Stendal       842
1184022676488314880 Polizei Pforzheim     283
1184024283342950401 Polizei Ravensburg    460
1232548941889228808 Systemstratege:       168
1295978598034284546 Polizei ZPD NI        133

[163 rows x 1 columns]